In [18]:
import json
import numpy as np
import xarray as xr
preg_num = int(sys.argv[1]) #7 # central europe

#####
preg = f'P{preg_num:02d}'

gcms_mesmer = [# 'ACCESS-CM2',  precipitation data not everywhere available , # 'MCM-UA-1-0', no precipitation data
               'ACCESS-ESM1-5', 'CESM2-WACCM', 'CESM2', 'CMCC-CM2-SR5', 'CNRM-CM6-1-HR',
               'CNRM-CM6-1', 'CNRM-ESM2-1', 'CanESM5', 'E3SM-1-1', 'FGOALS-f3-L',
               'FGOALS-g3', 'HadGEM3-GC31-LL', 'HadGEM3-GC31-MM', 'IPSL-CM6A-LR', 'MPI-ESM1-2-HR',
               'MPI-ESM1-2-LR' , 'MRI-ESM2-0', 'NorESM2-LM', 'NorESM2-MM', 'UKESM1-0-LL']

quantiles = ['0.05', '0.25', '0.5', '0.75', '0.95']
scenarios = ['CurPol', 'GS', 'LD','ModAct','Ref','Ren','Neg', 'SP','ssp119','ssp534-over']
path = '/home/www/lschuster/provide/MESMER-M_projections/runs/output/oggm_v16/2023.3/2100'


DATE = 'Jan29_2024'

f = open('/home/www/lschuster/provide/provide_glacier_regions/rgi_ids_per_provide_region.json')
rgis_preg = json.load(f)[preg]
rgis_preg = list(set(rgis_preg)) # the IDs are not unique ... 
rgis_preg = np.sort(rgis_preg) # make sure that the RGIs are sorted ...
print(preg, len(rgis_preg))
if preg == 'P03': # omit connectiity level 2 from P03 (i.e., Greenland)
    odf_preg = odf.loc[rgis_preg]
    odf_preg_sel = odf_preg.loc[odf_preg['Connect'] != 2]
    rgis_preg = odf_preg_sel.index
ds_model_s_ = []
for scenario in scenarios:
    ds_model_q_ = []
    for q in quantiles:
        ds_model_ = []
        for model in gcms_mesmer:
            dt_ = []
            for j in np.arange(0,int(np.ceil(len(rgis_preg)/500)),1):
                ji= j*500
                je = (j+1)*500
                with xr.open_dataset(f'{path}/{preg}/run_hydro_w5e5_gcm_merged_{scenario}_{model}_q{q}_bc_2000_2019_Batch_{ji}_{je}.nc') as dt:
                    dtx = dt[['volume']].load()
                    dt.close()
                dt = dt.sortby('rgi_id')
                dt_.append(dt)
            ds = xr.concat(dt_, dim ='rgi_id')
            ds['gcm'] = model 
            ds_model_.append(ds)
        ds_model_c = xr.concat(ds_model_, dim='gcm')
        ds_model_c['quantile'] = q
        ds_model_q_.append(ds_model_c)
    ds_model_sel = xr.concat(ds_model_q_, dim='quantile')
    ds_model_sel['scenario'] = scenario
    ds_model_s_.append(ds_model_sel)
    print(scenario)
ds_model = xr.concat(ds_model_s_, dim='scenario')
n = len(ds_model.rgi_id.values)
area_sum = odf.loc[ds_model.rgi_id.values]['Area'].sum()
assert n == len(rgis_preg)
assert set(rgis_preg) ==  set(ds_model.rgi_id.values)
# only common running glaicers ... 
ds_model = ds_model.volume.dropna(dim='rgi_id', how='any')
rgi_ids_preg = ds_model.rgi_id.values
area_sum_working = odf.loc[rgi_ids_preg]['Area'].sum()

ds_model = ds_model.sum(dim='rgi_id')
ds_model.attrs['n_rgi_ids'] = n
ds_model.attrs['n_rgi_ids_working'] = len(rgi_ids_preg)
ds_model.attrs['rgi_ids_working'] = rgi_ids_preg
ds_model.attrs['area_at_rgi_rgi_ids'] = area_sum
ds_model.attrs['area_at_rgi_rgi_ids_working'] = area_sum_working
print(preg, len(rgi_ids_preg), n, area_sum_working, area_sum)

ds_model.to_netcdf(f'/home/www/lschuster/provide/MESMER-M_projections/runs/volume_{preg}_aggregated_v{DATE}.nc')

In [19]:
p = 4

P04 4033
CurPol
GS
